In [1]:
%%capture

import warnings

warnings.filterwarnings("ignore")

import altair as alt
import branca
import branca.colormap as cm

import calitp_data_analysis.magics
import geopandas as gpd
import google.auth
import pandas as pd
from IPython.display import HTML, Image, Markdown, display, display_html
from omegaconf import OmegaConf
from update_vars import GTFS_DATA_DICT, RT_SCHED_GCS, SCHED_GCS, SEGMENT_GCS
from shared_utils import webmap_utils

readable_dict = OmegaConf.load("readable2.yml")
credentials, project = google.auth.default()

import _operator_grain_route_summary
import _operator_grain_route_dir_visuals as _report_operator_visuals
import _operator_grain_scheduled_service as _scheduled_service_hour_visuals

In [2]:
pd.options.display.max_columns = 100
pd.options.display.float_format = "{:.2f}".format
pd.set_option("display.max_rows", None)
pd.set_option("display.max_colwidth", None)

In [3]:
def formatted(number):
    return "{:,}".format(number)

In [4]:
analysis_name = "University of California, Davis"

In [5]:
# %%capture_parameters
# analysis_name

In [6]:
# Set drop down menu to be on the upper right for the charts
display(
    HTML(
        """
<style>
form.vega-bindings {
  position: absolute;
  right: 0px;
  top: 0px;
}
</style>
"""
    )
)

In [7]:
ROUTE_DIR_MONTH_FILE = GTFS_DATA_DICT.digest_tables.monthly_route_schedule_vp_report
OPERATOR_PROFILES = GTFS_DATA_DICT.digest_tables.operator_profiles_report
OPERATOR_ROUTE_MAP = GTFS_DATA_DICT.digest_tables.operator_routes_map_report
SCHEDULED_SERVICES = GTFS_DATA_DICT.digest_tables.scheduled_service_hours_report
ROUTE_DIR_QTR_FILE = GTFS_DATA_DICT.digest_tables.quarterly_route_schedule_vp_report

In [8]:
route_dir_month_df = pd.read_parquet(
    f"{RT_SCHED_GCS}{ROUTE_DIR_MONTH_FILE}.parquet",
    filters=[[("Analysis Name", "==", analysis_name)]],
).drop_duplicates()

In [9]:
route_dir_qtr_df = pd.read_parquet(
    f"{RT_SCHED_GCS}{ROUTE_DIR_QTR_FILE}.parquet",
    filters=[[("Analysis Name", "==", analysis_name)]],
)

In [10]:
route_df = gpd.read_parquet(
    f"{RT_SCHED_GCS}{OPERATOR_ROUTE_MAP}.parquet",
    filters=[[("analysis_name", "==", analysis_name)]],
    storage_options={"token": credentials.token},
)

In [11]:
# Add number column so we can plot this map using the webmap app
route_df = (route_df
                          .reset_index(drop=False)
                          .rename(columns={"index": "Number"})
                         )

In [12]:
profile_df = pd.read_parquet(
    f"{RT_SCHED_GCS}{OPERATOR_PROFILES}.parquet",
    filters=[[("analysis_name", "==", analysis_name)]],
)

In [29]:
profile_df.sample()

analysis_name service_date  \
168  University of California, Davis   2025-10-15   

                caltrans_district  operator_n_routes  operator_n_trips  \
168  03 - Marysville / Sacramento                 19              1016   

     operator_n_shapes  operator_n_stops  operator_n_arrivals  \
168                 43               270                12314   

     operator_route_length_miles  n_downtown_local_routes  n_local_routes  \
168                        88.06                       11               3   

     n_coverage_routes  n_rapid_routes  n_express_routes  n_rail_routes  \
168                  3              13                 2              0   

     n_ferry_routes  vp_per_min_agency  spatial_accuracy_agency  n_feeds  \
168               0               2.38                    95.81        1   

        operator_feeds counties_served  service_area_pop  \
168  Unitrans Schedule     Yolo County             70827   

     service_area_sq_miles hq_city  reporter_type primary_uza_name  
168                     11   Davis  Full Reporter        Davis, CA

In [13]:
service_hours_df = pd.read_parquet(
    f"{RT_SCHED_GCS}{SCHEDULED_SERVICES}.parquet",
    filters=[[("Analysis Name", "==", analysis_name)]],
)

In [14]:
analysis_name_edited = analysis_name.replace(" ","_").lower()
operator_webmap_file = f"{analysis_name_edited}_routes"

# {analysis_name}

## Operator Overview

In [15]:
try:
    date = profile_df["service_date"].dt.to_pydatetime()[0]
except:
    pass

In [16]:
try:
    service_area = formatted(int(profile_df.service_area_sq_miles.values[0]))
    service_pop = formatted(int(profile_df.service_area_pop.values[0]))
except:
    pass

In [17]:
try:
    display(
        Markdown(
            f"""{analysis_name} is headquartered in <b>{profile_df.hq_city.values[0]}</b> in the Urbanized Area of <b>{profile_df.primary_uza_name.values[0]}</b>.<br>
            This operator provides <b>{service_area}</b> square miles of public transit service, which has a service population of <b>{service_pop}</b>.<br>
            This organization is a {profile_df.reporter_type.values[0]}.<br>
            <b>Data Source</b>: <a href="https://www.transit.dot.gov/ntd/data-product/2022-annual-database-agency-information">National Transit Database</a> Annual Agency Information.
            """
        )
    )
except:
    pass

University of California, Davis is headquartered in <b>Davis</b> in the Urbanized Area of <b>Davis, CA</b>.<br>
            This operator provides <b>11</b> square miles of public transit service, which has a service population of <b>70,827</b>.<br>
            This organization is a Full Reporter.<br>
            <b>Data Source</b>: <a href="https://www.transit.dot.gov/ntd/data-product/2022-annual-database-agency-information">National Transit Database</a> Annual Agency Information.
            

### Route Typologies

In [18]:
try:
    display(
        Markdown(
            f"""The following data presents an overview of GTFS characteristics using data from the most recent date of
      <b>{date.strftime("%B")} {date.year}</b>."""
        )
    )
except:
    pass

The following data presents an overview of GTFS characteristics using data from the most recent date of
      <b>October 2025</b>.

In [19]:
try:
    n_routes = formatted(profile_df["operator_n_routes"].values[0])
    display(
        Markdown(
            f"""{analysis_name} runs <b>{n_routes}</b> unique routes. Below is the breakdown of the routes and routes can belong to one or more categories.<p>
            Route categories are determined using a approach that looks at GTFS trips data
        alongside National Association of City Transportation Officials (NACTO)'s
        <a href="https://nacto.org/publication/transit-street-design-guide/introduction/service-context/transit-route-types/">Transit Route Types</a> 
        and <a href= "https://nacto.org/publication/transit-street-design-guide/introduction/service-context/transit-frequency-volume/">Frequency and Volume</a>
        guides. Please see the <a href="https://github.com/cal-itp/data-analyses/blob/main/gtfs_digest/methodology.md">methodology docs</a> for more details on this approach.
        """
        )
    )
except:
    display(Markdown(f"""{analysis_name} doesn't have an operator profile."""))

University of California, Davis runs <b>19</b> unique routes. Below is the breakdown of the routes and routes can belong to one or more categories.<p>
            Route categories are determined using a approach that looks at GTFS trips data
        alongside National Association of City Transportation Officials (NACTO)'s
        <a href="https://nacto.org/publication/transit-street-design-guide/introduction/service-context/transit-route-types/">Transit Route Types</a> 
        and <a href= "https://nacto.org/publication/transit-street-design-guide/introduction/service-context/transit-frequency-volume/">Frequency and Volume</a>
        guides. Please see the <a href="https://github.com/cal-itp/data-analyses/blob/main/gtfs_digest/methodology.md">methodology docs</a> for more details on this approach.
        

In [20]:
try:
    display(_operator_grain_route_summary.route_typology_chart(profile_df))
except:
    display(
        Markdown(f"""{analysis_name} doesn't have route typology data available.""")
    )

alt.Chart(...)

### Service Area

In [21]:
color_map = cm.linear.Spectral_11.scale(0, len(route_df))

In [30]:
try:
    operator_map = webmap_utils.set_state_export(
    route_df[["Route","geometry", "Number"]],
    subfolder = "operator_digest/",
    filename=operator_webmap_file,
    map_title=f"Transit Routes for {analysis_name}",
    cmap=color_map,
    color_col="Number",
    overwrite = True
    )
    display(webmap_utils.render_spa_link(operator_map["spa_link"], text=f"Routes for {analysis_name}"))
    display(webmap_utils.display_spa_map(operator_map["spa_link"]))
except:
    display(Markdown(f"""{analysis_name} doesn't have an route geographies."""))

<a href="https://embeddable-maps.calitp.org/?state=eyJuYW1lIjogIm51bGwiLCAibGF5ZXJzIjogW3sibmFtZSI6ICJUcmFuc2l0IFJvdXRlcyBmb3IgVW5pdmVyc2l0eSBvZiBDYWxpZm9ybmlhLCBEYXZpcyIsICJ1cmwiOiAiaHR0cHM6Ly9zdG9yYWdlLmdvb2dsZWFwaXMuY29tL2NhbGl0cC1tYXAtdGlsZXMvb3BlcmF0b3JfZGlnZXN0L3VuaXZlcnNpdHlfb2ZfY2FsaWZvcm5pYSxfZGF2aXNfcm91dGVzLmdlb2pzb24uZ3oiLCAicHJvcGVydGllcyI6IHsic3Ryb2tlZCI6IGZhbHNlLCAiaGlnaGxpZ2h0X3NhdHVyYXRpb25fbXVsdGlwbGllciI6IDAuNX19XSwgImxhdF9sb24iOiBbMzguNTQ4OTcyNzE0NzM4MjYsIC0xMjEuNzQ3OTc2MzkwMzgwOTddLCAiem9vbSI6IDEzfQ==" target="_blank">Open Routes for University of California, Davis in New Tab</a>

None

None

In [23]:
try:
    n_service_miles = formatted(int(profile_df.operator_route_length_miles.values[0]))
    n_stops = formatted(int(profile_df["operator_n_stops"].values[0]))
    n_arrivals = formatted(int(profile_df["operator_n_arrivals"].values[0]))

    display(
        Markdown(
            f"""{analysis_name} provides <b>{n_service_miles}</b> miles of public transit in {profile_df['counties_served'].values[0]} counties.
            {analysis_name} stops at <b>{n_stops}</b> unique stops, 
                totaling to <b>{n_arrivals}</b> arrivals.
        """
        )
    )

except:
    pass

University of California, Davis provides <b>88</b> miles of public transit in Yolo County counties.
            University of California, Davis stops at <b>270</b> unique stops, 
                totaling to <b>12,314</b> arrivals.
        

In [24]:
try:
    display(_operator_grain_route_summary.percentile_routes_chart(route_df))
except:
    pass

alt.LayerChart(...)

### Service Hours 

In [25]:
try:
    display(
        _scheduled_service_hour_visuals.scheduled_service_hr_graph(
            service_hours_df, "Weekday", readable_dict.weekday_scheduled_service_graph
        )
    )
except:
    pass

alt.LayerChart(...)

In [26]:
try:
    display(
        _scheduled_service_hour_visuals.scheduled_service_hr_graph(
            service_hours_df, "Saturday", readable_dict.saturday_scheduled_service_graph
        )
    )
except:
    pass

alt.LayerChart(...)

In [27]:
try:
    display(
        _scheduled_service_hour_visuals.scheduled_service_hr_graph(
            service_hours_df, "Sunday", readable_dict.sunday_scheduled_service_graph
        )
    )
except:
    pass

alt.LayerChart(...)

## Detailed Route Overview

In [28]:
try:
    display(
        _report_operator_visuals.route_filter(route_dir_qtr_df, route_dir_month_df)
    )
except:
    display(Markdown(f"""{analysis_name} only has schedule data."""))

alt.VConcatChart(...)